# Inspect data and search for failed simulations

In [1]:
import os
import re
import sys

import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from  plotly import colors
import pandas as pd

from rdkit import Chem
from rdkit.Chem import Draw, PandasTools, rdDepictor
from rdkit.Chem.Draw import rdMolDraw2D, IPythonConsole

rdDepictor.SetPreferCoordGen(True)
from IPython.display import SVG
import rdkit

from svgutils import transform as sg

from IPython.core.display import HTML
from scipy.stats import norm

from PLBenchmarks import targets, ligands, edges

from tqdm.notebook import tqdm

sys.path.append(os.path.join(os.getcwd(), '..'))
import benchmarkpl
path = benchmarkpl.__path__[0]
targets.set_data_dir(path)

# Read in data for Parsley forcefield

Function to read in data

In [2]:
from benchmarkpl import load_data

In [3]:
df = load_data.getDetailedResults('shp2')
df.head()

leg   water                   complex        \
                              repeat       1                         1         
                  Unnamed: 0_level_2     val   err  aerr  conv     val   err   
edge_SHP099-1_E8    edge_SHP099-1_E8   54.65  0.11  0.12  0.09   55.94  0.31   
edge_SHP099-1_E14  edge_SHP099-1_E14   34.56  0.26  0.29  0.17   31.26  0.39   
edge_SHP099-1_E22  edge_SHP099-1_E22   16.87  0.10  0.10 -0.00   19.97  0.17   
edge_SHP099-1_E2    edge_SHP099-1_E2 -294.52  0.10  0.08 -0.09 -294.73  0.16   
edge_SHP099-1_E1    edge_SHP099-1_E1 -296.82  0.08  0.08 -0.04 -298.13  0.16   

                                ddg             ddg_mean                 lig1  \
                                  1                    -                        
                   aerr  conv   val   err  aerr      val   err aerr             
edge_SHP099-1_E8   0.34  0.15  1.29  0.33  0.36     1.29  0.33  NaN  SHP099-1   
edge_SHP099-1_E14  0.86  0.78 -3.30  0.47  0.91    -3.30  0.47  NaN  SHP099-1   
edge_SHP099-1_E22  0.27  0.32  3.10  0.20  0.29     3.10  0.20  NaN  SHP099-1   
edge_SHP099-1_E2   0.20  0.20 -0.21  0.19  0.22    -0.21  0.19  NaN  SHP099-1   
edge_SHP099-1_E1   0.18  0.01 -1.31  0.18  0.20    -1.31  0.18  NaN  SHP099-1   

                  lig2 exp_DDG dexp_DDG  
                                         
                                         
edge_SHP099-1_E8    E8    0.04      0.0  
edge_SHP099-1_E14  E14   -0.03      0.0  
edge_SHP099-1_E22  E22    0.51      0.0  
edge_SHP099-1_E2    E2    1.48      0.0  
edge_SHP099-1_E1    E1    0.77      0.0

# load all data into one dataframe

In [21]:
forcefield = 'openff-1.0.0.offxml'
dfs = []
for target in tqdm(targets.target_dict):
    df = load_data.getDetailedResults(target, forcefield=forcefield)
    if df is None:
        continue
    for env in ['complex', 'water']:
        for rep in range(1,4):
            if str(rep) in df.columns.get_level_values(1):
                sub_df = df.loc[:, (env, str(rep), slice(None))].copy()
                sub_df.columns = sub_df.columns.get_level_values(2)
                sub_df['env'] = env
                sub_df['repeat'] = rep
                sub_df['target'] = target
                sub_df['edge'] = sub_df.index
                sub_df.reset_index(drop=True, inplace=True)
                dfs.append(sub_df)
all_sims = pd.concat(dfs, ignore_index=True)
all_sims.reset_index(drop=True, inplace=True)
all_sims.head()

val   err  aerr  conv      env  repeat target                  edge
0 -7.31  0.07  0.09  0.12  complex       1   jnk1  edge_17124-1_18634-1
1  0.72  0.14  0.11 -0.15  complex       1   jnk1  edge_18626-1_18624-1
2 -0.41  0.12  0.15  0.13  complex       1   jnk1  edge_18636-1_18625-1
3  6.10  0.07  0.09  0.12  complex       1   jnk1  edge_18632-1_18624-1
4  2.48  0.09  0.08 -0.03  complex       1   jnk1  edge_18635-1_18625-1

# Filter out simulations with run issues (nan values as results)

In [22]:
isna = all_sims.isna()
all_sims['failed'] = False
for i, row in isna.iterrows():
    if np.any(row):
        all_sims.loc[i, 'failed'] = True
print(f'There are {all_sims.loc[all_sims["failed"]].shape[0]} failed out of {all_sims.shape[0]} simulations')
all_sims.loc[all_sims['failed']]

There are 110 failed out of 5112 simulations


val  err  aerr  conv      env  repeat target  \
1365  NaN  NaN   NaN   NaN  complex       2   cmet   
1366  NaN  NaN   NaN   NaN  complex       2   cmet   
1367  NaN  NaN   NaN   NaN  complex       2   cmet   
1368  NaN  NaN   NaN   NaN  complex       2   cmet   
1369  NaN  NaN   NaN   NaN  complex       2   cmet   
...   ...  ...   ...   ...      ...     ...    ...   
4609  NaN  NaN   NaN   NaN    water       2  pde10   
4620  NaN  NaN   NaN   NaN    water       3  pde10   
4632  NaN  NaN   NaN   NaN    water       3  pde10   
4633  NaN  NaN   NaN   NaN    water       3  pde10   
4671  NaN  NaN   NaN   NaN    water       3  pde10   

                                                   edge  failed  
1365  edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL34...    True  
1366  edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL34...    True  
1367  edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL34...    True  
1368  edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL34...    True  
1369  edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL34...    True  
...                                                 ...     ...  
4609                                     edge_3484_4189    True  
4620                                     edge_7395_3484    True  
4632                                     edge_3806_5973    True  
4633                             edge_3806-mvEster_5973    True  
4671                                     edge_3484_4189    True  

[110 rows x 9 columns]

In [23]:
unique_failed_edges = {}

for i, row in tqdm(all_sims.loc[all_sims['failed']].iterrows()):
    target = row['target']
    edge = row['edge']
    env = row['env']
    repeat= row ['repeat']
    if not target in unique_failed_edges:
        unique_failed_edges[target] = {}
    if not edge in unique_failed_edges[target]:
        unique_failed_edges[target][edge] = {}
    if not env in unique_failed_edges[target][edge]:
        unique_failed_edges[target][edge][env] = []
    unique_failed_edges[target][edge][env].append(repeat)
unique_failed_edges

{'cmet': {'edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL3402744_300_4': {'complex': [2,
    3],
   'water': [2, 3]},
  'edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL3402745_200_5': {'complex': [2,
    3],
   'water': [2, 3]},
  'edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL3402743_42': {'complex': [2, 3],
   'water': [2, 3]},
  'edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL3402764_90': {'complex': [2, 3],
   'water': [2, 3]},
  'edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL3402760_1': {'complex': [2, 3],
   'water': [2, 3]},
  'edge_CHEMBL3402765_11-charged-pKa-8.1_CHEMBL3402742_23': {'complex': [2, 3],
   'water': [2, 3]},
  'edge_CHEMBL3402761_1_21_CHEMBL3402760_1': {'complex': [2, 3],
   'water': [2, 3]},
  'edge_CHEMBL3402761_1_21_CHEMBL3402762_1': {'complex': [2], 'water': [2, 3]},
  'edge_CHEMBL3402762_1_CHEMBL3402760_1': {'complex': [2], 'water': [2, 3]},
  'edge_CHEMBL3402742_23_CHEMBL3402763_90': {'complex': [2, 3],
   'water': [2, 3]},
  'edge_CHEMBL3402742_23_CHEMBL3402756_2.7': 

In [24]:
from benchmarkpl import drawing

d2ds = []
if os.path.exists('../../../02_benchmark_calculations/'):
    targets.set_data_dir('../../../02_benchmark_calculations/')
for target in unique_failed_edges.keys():
    eSet = edges.EdgeSet(target)
    for edge in unique_failed_edges[target].keys():
        df = eSet[edge].get_dataframe()
        df['target'] = target
        
        text = ''
        for env in unique_failed_edges[target][edge].keys():
            text+=(f'{env} (repeats {", ".join([str(rep) for rep in unique_failed_edges[target][edge][env]])}), ')
        text += f'DDG_exp = {df["exp. DeltaG [kcal/mol]"].magnitude}'\
            f' ({df["exp. Error [kcal/mol]"].magnitude}) kcal/mol'
        
        # check whether image exists
        os.makedirs(os.path.join(path, targets.get_target_dir(target), '11_failed'), exist_ok=True)
        file_path = os.path.join(path, targets.get_target_dir(target), '11_failed', f'{edge}.svg')
        if os.path.exists(file_path):
            with open(file_path, 'r') as file:
                img = file.read()
        else:
            # visualization
            m1 = Chem.SDMolSupplier(f'{targets.data_path}/{targets.get_target_dir(target)}/02_ligands/lig_{df[0]}/crd/lig_{df[0]}.sdf', removeHs=False)[0]
            m2 = Chem.SDMolSupplier(f'{targets.data_path}/{targets.get_target_dir(target)}/02_ligands/lig_{df[1]}/crd/lig_{df[1]}.sdf', removeHs=False)[0]
            pairs = np.loadtxt(f'{targets.data_path}/{targets.get_target_dir(target)}/03_hybrid/edge_{df[0]}_{df[1]}/water/crd/pairs.dat')
            # decrement pairs to match rdkit counting from 0!
            pairs -= 1
            img = drawing.drawPerturbation(m1, # rdkit molecule 1
                                           m2, # rdkit molecule 2
                                           pairs, # pairs, np array or list of lists
                                           target=target, # string with target name
                                           n1=df[0], # name mol 1
                                           n2=df[1], # name  mol 2
                                           text=text# additional text
                                  )

            with open(file_path, 'w') as file:
                file.write(img)
        #df['img'] = drawPerturbation(m1, m2, pairs, target=t, n1=df[0], n2=df[1]).GetDrawingText()
        d2ds.append(img)

HTML(''.join(d2ds))

In [25]:
#HTML(nanEdges.to_html())

In [26]:
#save failed edges to separate csv file and remove them from dataframe
all_sims.loc[all_sims['failed']].to_csv(f'failed_simulations_{forcefield}.csv')
all_sims = all_sims.drop(labels=all_sims.loc[all_sims['failed']].index, axis=0)
all_sims.head()

val   err  aerr  conv      env  repeat target                  edge  \
0 -7.31  0.07  0.09  0.12  complex       1   jnk1  edge_17124-1_18634-1   
1  0.72  0.14  0.11 -0.15  complex       1   jnk1  edge_18626-1_18624-1   
2 -0.41  0.12  0.15  0.13  complex       1   jnk1  edge_18636-1_18625-1   
3  6.10  0.07  0.09  0.12  complex       1   jnk1  edge_18632-1_18624-1   
4  2.48  0.09  0.08 -0.03  complex       1   jnk1  edge_18635-1_18625-1   

   failed  
0   False  
1   False  
2   False  
3   False  
4   False

In [27]:
# save finished simulations
all_sims.to_csv(f'finished_simulations_{forcefield}.csv')

# Look at convergence criteria and set a criterion

In [28]:
# Extract convergence 
conv_thres = 0.8
all_sims['bConv'] = all_sims['conv'] < conv_thres
print(f'Simulations converged (Convergence < {conv_thres}):\n\
in water: {all_sims["bConv"].loc[all_sims["env"]=="water"].sum()} \
out of {all_sims.loc[all_sims["env"]=="water"].shape[0]}\n\
in complex: {all_sims["bConv"].loc[all_sims["env"]=="complex"].sum()} \
out of {all_sims.loc[all_sims["env"]=="complex"].shape[0]} simulations.')

Simulations converged (Convergence < 0.8):
in water: 2456 out of 2500
in complex: 2239 out of 2502 simulations.


In [29]:
# Extract convergence
err_thres = 1.0
all_sims['bErr'] = (all_sims['err'] < err_thres).values
print(f'Simulations converged (Bootstrap error < {err_thres}):\n\
in water: {all_sims["bErr"].loc[all_sims["env"]=="water"].sum()} \
out of {all_sims.loc[all_sims["env"]=="water"].shape[0]}\n\
in complex: {all_sims["bErr"].loc[all_sims["env"]=="complex"].sum()} \
out of {all_sims.loc[all_sims["env"]=="complex"].shape[0]} simulations.')

Simulations converged (Bootstrap error < 1.0):
in water: 2499 out of 2500
in complex: 2477 out of 2502 simulations.


In [30]:
# Extract convergence
aerr_thres = 1.0
all_sims['bAerr'] = (all_sims['aerr'] < aerr_thres).values
print(f'Simulations converged (Analytical error < {aerr_thres}):\n\
in water: {all_sims["bAerr"].loc[all_sims["env"]=="water"].sum()} \
out of {all_sims.loc[all_sims["env"]=="water"].shape[0]}\n\
in complex: {all_sims["bAerr"].loc[all_sims["env"]=="complex"].sum()} \
out of {all_sims.loc[all_sims["env"]=="complex"].shape[0]} simulations.')

Simulations converged (Analytical error < 1.0):
in water: 2469 out of 2500
in complex: 2278 out of 2502 simulations.


In [31]:
all_sims['include'] = all_sims['bAerr'] & all_sims['bConv']
print(f'Included simulations:\n\
in water: {all_sims["include"].loc[all_sims["env"]=="water"].sum()} \
out of {all_sims.loc[all_sims["env"]=="water"].shape[0]}\n\
in complex: {all_sims["include"].loc[all_sims["env"]=="complex"].sum()} \
out of {all_sims.loc[all_sims["env"]=="complex"].shape[0]} simulations.')

Included simulations:
in water: 2455 out of 2500
in complex: 2230 out of 2502 simulations.


In [32]:
import itertools
import plotly
cols = plotly.colors.DEFAULT_PLOTLY_COLORS

fig = make_subplots(rows=2, cols=2, shared_xaxes=True, shared_yaxes=True)

# Add traces
col = 0
for env, rep in itertools.product(['water', 'complex'], ['1', '2', '3']):
    idx = np.logical_and(all_sims['env']==env, all_sims['repeat'] == int(rep))
    conv = all_sims.loc[idx, 'conv']
    aerr = all_sims.loc[idx, 'aerr']
    err = all_sims.loc[idx, 'err']
    text = [f'{row["target"]}:{row["edge"]}' for i, row in all_sims.loc[idx].iterrows()]
    fig.add_trace(go.Scatter(x=conv, y=aerr,
                    mode='markers',
                    hovertext=text,
                    name=f'{env}{rep}',
                    opacity=.8,
                    marker_color=cols[col]), 
                 col=1,
                 row=1)
    fig.add_trace(go.Scatter(x=aerr, y=err,
                    mode='markers',
                    hovertext=text,
                    name=f'{env}{rep}',
                    marker_color=cols[col],
                    opacity=.8,
                    showlegend=False), 
                 col=2,
                 row=2)
    fig.add_trace(go.Scatter(x=conv, y=err,
                    mode='markers',
                    hovertext=text,
                    name=f'{env}{rep}',
                    opacity=.8,
                    marker_color=cols[col],
                    showlegend=False), 
                 col=1,
                 row=2)
    col += 1
fig.add_trace(go.Scatter(x=all_sims.loc[np.invert(all_sims['include']), 'conv'], 
                         y=all_sims.loc[np.invert(all_sims['include']), 'aerr'],
            mode='markers',
            name=f'not converged',
            opacity=.8,
                         marker_size=3,
            marker_color='black',
            showlegend=False), 
         col=1,
         row=1)
fig.add_trace(go.Scatter(x=all_sims.loc[np.invert(all_sims['include']), 'conv'], 
                         y=all_sims.loc[np.invert(all_sims['include']), 'err'],
            mode='markers',
            name=f'not converged',
            opacity=.8,
                         marker_size=3,
            marker_color='black',
            showlegend=False), 
         col=1,
         row=2)
fig.add_trace(go.Scatter(x=all_sims.loc[np.invert(all_sims['include']), 'aerr'], 
                         y=all_sims.loc[np.invert(all_sims['include']), 'err'],
            mode='markers',
            name=f'not converged',
            opacity=.8,
                         marker_size=3,
            marker_color='black',
            showlegend=False), 
         col=2,
         row=2)
fig.update_layout(
    yaxis3 = dict(title='Bootstrap Error [kcal mol<sup>-1</sup>]'),
    xaxis3=dict(title='Convergence'), 
    yaxis=dict(range=[0,5], title='Analytical Error [kcal mol<sup>-1</sup>]'),
    xaxis4=dict(range=[0,5], title='Analytical Error [kcal mol<sup>-1</sup>]'),)
fig.show()

In [33]:
unique_nonconverged_edges = {}

for i, row in tqdm(all_sims.loc[np.invert(all_sims['include'])].iterrows()):
    target = row['target']
    edge = row['edge']
    env = row['env']
    repeat= row ['repeat']
    if not target in unique_nonconverged_edges:
        unique_nonconverged_edges[target] = {}
    if not edge in unique_nonconverged_edges[target]:
        unique_nonconverged_edges[target][edge] = {}
    if not env in unique_nonconverged_edges[target][edge]:
        unique_nonconverged_edges[target][edge][env] = []
    unique_nonconverged_edges[target][edge][env].append(repeat)
unique_nonconverged_edges

{'jnk1': {'edge_18631-1_18660-1': {'complex': [3]}},
 'pde2': {'edge_49220548_49932129': {'complex': [1]},
  'edge_49175828_49580115': {'complex': [1]},
  'edge_48168913_49585367': {'complex': [1, 2, 3]},
  'edge_49932714_49137530': {'complex': [2]},
  'edge_49220548_49580115': {'complex': [2]},
  'edge_43249674_49175789': {'complex': [2]},
  'edge_49220392_49175828': {'complex': [3]},
  'edge_50181001_49582390': {'complex': [3]},
  'edge_49932714_49175789': {'complex': [3]},
  'edge_49932714_49582468': {'complex': [3]},
  'edge_49175789_49072088': {'complex': [3]}},
 'thrombin': {'edge_1a_3b': {'complex': [3]}},
 'p38': {'edge_p38a_2u_p38a_2q': {'complex': [1, 2, 3]},
  'edge_p38a_2u_p38a_2k': {'complex': [1, 2, 3], 'water': [1, 3]},
  'edge_p38a_2z_p38a_3fmk': {'complex': [1, 2, 3]},
  'edge_p38a_3flz_p38a_2c': {'complex': [1, 3]},
  'edge_p38a_2z_p38a_3flq': {'complex': [1, 2, 3], 'water': [2]},
  'edge_p38a_2z_p38a_3flw': {'complex': [2, 3]},
  'edge_p38a_2v_p38a_3fmk': {'complex':

In [34]:
d2ds = []
if os.path.exists('../../../02_benchmark_calculations/'):
    targets.set_data_dir('../../../02_benchmark_calculations/')
for target in unique_nonconverged_edges.keys():
    eSet = edges.EdgeSet(target)
    for edge in unique_nonconverged_edges[target].keys():
        df = eSet[edge].get_dataframe()
        df['target'] = target
        
        text = ''
        for env in unique_nonconverged_edges[target][edge].keys():
            text+=(f'{env} (repeats {", ".join([str(rep) for rep in unique_nonconverged_edges[target][edge][env]])}), ')
        text += f'DDG_exp = {df["exp. DeltaG [kcal/mol]"].magnitude}'\
            f' ({df["exp. Error [kcal/mol]"].magnitude}) kcal/mol'
        
        # check whether image exists
        os.makedirs(os.path.join(path, targets.get_target_dir(target), '12_not_converged'), exist_ok=True)
        file_path = os.path.join(path, targets.get_target_dir(target), '12_not_converged', f'{edge}.svg')
        if os.path.exists(file_path):
            with open(file_path, 'r') as file:
                img = file.read()
        else:
            # visualization
            m1 = Chem.SDMolSupplier(f'{targets.data_path}/{targets.get_target_dir(target)}/02_ligands/lig_{df[0]}/crd/lig_{df[0]}.sdf', removeHs=False)[0]
            m2 = Chem.SDMolSupplier(f'{targets.data_path}/{targets.get_target_dir(target)}/02_ligands/lig_{df[1]}/crd/lig_{df[1]}.sdf', removeHs=False)[0]
            pairs = np.loadtxt(f'{targets.data_path}/{targets.get_target_dir(target)}/03_hybrid/edge_{df[0]}_{df[1]}/water/crd/pairs.dat')
            # decrement pairs to match rdkit counting from 0!
            pairs -= 1
            img = drawing.drawPerturbation(m1, # rdkit molecule 1
                                   m2, # rdkit molecule 2
                                   pairs, # pairs, np array or list of lists
                                   target=target, # string with target name
                                   n1=df[0], # name mol 1
                                   n2=df[1], # name  mol 2
                                   text=text# additional text
                                  )

            with open(file_path, 'w') as file:
                file.write(img)
        #df['img'] = drawPerturbation(m1, m2, pairs, target=t, n1=df[0], n2=df[1]).GetDrawingText()
        d2ds.append(img)

HTML(''.join(d2ds))

OSError: File error: Bad input file /projects/CNS/OGA/FEP_compare/openforcefield/02_benchmark_calculations/2019-12-13_cmet_original/02_ligands/lig_CHEMBL3402754_40_14/crd/lig_CHEMBL3402754_40_14.sdf

# Filter out non-converged simulations

In [35]:
# remove non-converged simulations and save converged simulations to file
all_sims = all_sims.drop(labels=all_sims.loc[np.invert(all_sims['include'])].index, axis=0)
all_sims = all_sims.drop(labels=['include', 'failed', 'bConv', 'bErr', 'bAerr'], axis=1)
all_sims.to_csv(f'converged_simulations_{forcefield}.csv')
all_sims.head()

val   err  aerr  conv      env  repeat target                  edge
0 -7.31  0.07  0.09  0.12  complex       1   jnk1  edge_17124-1_18634-1
1  0.72  0.14  0.11 -0.15  complex       1   jnk1  edge_18626-1_18624-1
2 -0.41  0.12  0.15  0.13  complex       1   jnk1  edge_18636-1_18625-1
3  6.10  0.07  0.09  0.12  complex       1   jnk1  edge_18632-1_18624-1
4  2.48  0.09  0.08 -0.03  complex       1   jnk1  edge_18635-1_18625-1